In [1]:
import os
import librosa
import numpy as np
import tensorflow as tf
from sklearn.metrics import accuracy_score, confusion_matrix, classification_report
import matplotlib.pyplot as plt
import seaborn as sns
import tkinter as tk
from tkinter import filedialog, messagebox
import sounddevice as sd
from scipy.io.wavfile import write
import tempfile

In [2]:
# Dataset path
BASE_PATH = "C:/Users/NSPatil/OneDrive/Desktop/SEM VI/mp/Project code files and datasets/Sound"
TRAIN_PATH = os.path.join(BASE_PATH, "Training")
VAL_PATH = os.path.join(BASE_PATH, "Validation")

In [3]:
LABELS = ['background', 'gunshot']
SAMPLE_RATE = 8000  # Updated to match dataset
DURATION = 4.09  # Updated to match dataset
SAMPLES_PER_TRACK = int(SAMPLE_RATE * DURATION)
TARGET_SHAPE = (128, 128)

In [4]:
def extract_features(file_path, target_shape=TARGET_SHAPE):
    y, sr = librosa.load(file_path, sr=SAMPLE_RATE, duration=DURATION)
    if len(y) < SAMPLES_PER_TRACK:
        y = np.pad(y, (0, SAMPLES_PER_TRACK - len(y)))
    mel = librosa.feature.melspectrogram(y=y, sr=sr, n_mels=target_shape[0])
    mel_db = librosa.power_to_db(mel, ref=np.max)

    # Ensure fixed width
    if mel_db.shape[1] < target_shape[1]:
        pad_width = target_shape[1] - mel_db.shape[1]
        mel_db = np.pad(mel_db, ((0, 0), (0, pad_width)), mode='constant')
    else:
        mel_db = mel_db[:, :target_shape[1]]

    return mel_db

In [5]:
def load_dataset(folder_path):
    features = []
    labels = []
    for label_idx, label in enumerate(LABELS):
        class_folder = os.path.join(folder_path, label)
        if not os.path.exists(class_folder):
            print(f"🚫 Folder not found: {class_folder}")
            continue
        for file in os.listdir(class_folder):
            if file.lower().endswith(".wav"):  # ✅ handles .WAV and .wav
                file_path = os.path.join(class_folder, file)
                try:
                    mel_feature = extract_features(file_path)
                    if mel_feature.shape == TARGET_SHAPE:
                        features.append(mel_feature)
                        labels.append(label_idx)
                        print(f"✅ Loaded {file_path}, shape: {mel_feature.shape}")
                    else:
                        print(f"⚠️ Skipped {file_path}, unexpected shape: {mel_feature.shape}")
                except Exception as e:
                    print(f"❌ Failed to process {file_path}: {e}")
    print(f"📦 Loaded {len(features)} samples from {folder_path}")
    return np.array(features, dtype=np.float32), np.array(labels)


In [6]:
# Load datasets
X_train, y_train = load_dataset(TRAIN_PATH)
X_val, y_val = load_dataset(VAL_PATH)

✅ Loaded C:/Users/NSPatil/OneDrive/Desktop/SEM VI/mp/Project code files and datasets/Sound\Training\background\5B1E81C4.WAV, shape: (128, 128)
✅ Loaded C:/Users/NSPatil/OneDrive/Desktop/SEM VI/mp/Project code files and datasets/Sound\Training\background\5B1E81C7.WAV, shape: (128, 128)
✅ Loaded C:/Users/NSPatil/OneDrive/Desktop/SEM VI/mp/Project code files and datasets/Sound\Training\background\5B1E81DD.WAV, shape: (128, 128)
✅ Loaded C:/Users/NSPatil/OneDrive/Desktop/SEM VI/mp/Project code files and datasets/Sound\Training\background\5B1E8224.WAV, shape: (128, 128)
✅ Loaded C:/Users/NSPatil/OneDrive/Desktop/SEM VI/mp/Project code files and datasets/Sound\Training\background\5B1E8226.WAV, shape: (128, 128)
✅ Loaded C:/Users/NSPatil/OneDrive/Desktop/SEM VI/mp/Project code files and datasets/Sound\Training\background\5B1E8268.WAV, shape: (128, 128)
✅ Loaded C:/Users/NSPatil/OneDrive/Desktop/SEM VI/mp/Project code files and datasets/Sound\Training\background\5B1E826B.WAV, shape: (128, 128)

C:\Users\NSPatil\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\librosa\util\decorators.py:88: UserWarning: PySoundFile failed. Trying audioread instead.
  return f(*args, **kwargs)


✅ Loaded C:/Users/NSPatil/OneDrive/Desktop/SEM VI/mp/Project code files and datasets/Sound\Training\background\603F18FE.WAV, shape: (128, 128)
✅ Loaded C:/Users/NSPatil/OneDrive/Desktop/SEM VI/mp/Project code files and datasets/Sound\Training\background\603F1933.WAV, shape: (128, 128)
✅ Loaded C:/Users/NSPatil/OneDrive/Desktop/SEM VI/mp/Project code files and datasets/Sound\Training\background\603F1BC4.WAV, shape: (128, 128)
✅ Loaded C:/Users/NSPatil/OneDrive/Desktop/SEM VI/mp/Project code files and datasets/Sound\Training\background\603F2753.WAV, shape: (128, 128)
✅ Loaded C:/Users/NSPatil/OneDrive/Desktop/SEM VI/mp/Project code files and datasets/Sound\Training\background\603F2766.WAV, shape: (128, 128)
✅ Loaded C:/Users/NSPatil/OneDrive/Desktop/SEM VI/mp/Project code files and datasets/Sound\Training\background\603F29E3.WAV, shape: (128, 128)
✅ Loaded C:/Users/NSPatil/OneDrive/Desktop/SEM VI/mp/Project code files and datasets/Sound\Training\background\603F30DE.WAV, shape: (128, 128)

In [7]:
# Preprocessing
X_train = np.expand_dims(X_train, -1)
X_val = np.expand_dims(X_val, -1)
X_train = (X_train - 127.5) / 127.5
X_val = (X_val - 127.5) / 127.5

In [8]:
# Build model with MobileNetV2
base_model = tf.keras.applications.MobileNetV2(
    input_shape=(128, 128, 3),
    include_top=False,
    weights='imagenet')
base_model.trainable = False

In [9]:
model = tf.keras.Sequential([
    tf.keras.layers.Input(shape=(128, 128, 1)),
    tf.keras.layers.Conv2D(3, (3, 3), padding='same'),
    base_model,
    tf.keras.layers.GlobalAveragePooling2D(),
    tf.keras.layers.Dense(64, activation='relu'),
    tf.keras.layers.Dense(2, activation='softmax')
])

In [10]:
model.compile(optimizer='adam',
              loss='sparse_categorical_crossentropy',
              metrics=['accuracy'])

In [11]:
model.fit(X_train, y_train, epochs=20, validation_data=(X_val, y_val))

Epoch 1/20
900/900 ━━━━━━━━━━━━━━━━━━━━ 240s 256ms/step - accuracy: 0.9789 - loss: 0.0914 - val_accuracy: 0.9858 - val_loss: 0.0537
Epoch 2/20
900/900 ━━━━━━━━━━━━━━━━━━━━ 181s 201ms/step - accuracy: 0.9838 - loss: 0.0554 - val_accuracy: 0.9886 - val_loss: 0.0438
Epoch 3/20
900/900 ━━━━━━━━━━━━━━━━━━━━ 193s 215ms/step - accuracy: 0.9861 - loss: 0.0496 - val_accuracy: 0.9730 - val_loss: 0.0867
Epoch 4/20
900/900 ━━━━━━━━━━━━━━━━━━━━ 219s 243ms/step - accuracy: 0.9870 - loss: 0.0442 - val_accuracy: 0.9855 - val_loss: 0.0561
Epoch 5/20
900/900 ━━━━━━━━━━━━━━━━━━━━ 189s 210ms/step - accuracy: 0.9876 - loss: 0.0394 - val_accuracy: 0.9861 - val_loss: 0.0499
Epoch 6/20
900/900 ━━━━━━━━━━━━━━━━━━━━ 184s 204ms/step - accuracy: 0.9893 - loss: 0.0351 - val_accuracy: 0.9873 - val_loss: 0.0465
Epoch 7/20
900/900 ━━━━━━━━━━━━━━━━━━━━ 199s 221ms/step - accuracy: 0.9899 - loss: 0.0346 - val_accuracy: 0.9851 - val_loss: 0.0495
Epoch 8/20
900/900 ━━━━━━━━━━━━━━━━━━━━ 225s 250ms/step - accuracy: 0.9893 -

In [12]:
def predict_audio(file_path):
    try:
        mel = extract_features(file_path)
        mel = np.expand_dims(mel, axis=(0, -1))  # (1, 128, 128, 1)
        mel = (mel - 127.5) / 127.5
        #mel = tf.image.grayscale_to_rgb(tf.convert_to_tensor(mel))  # (1, 128, 128, 3)
        prediction = model.predict(mel)
        predicted_class = LABELS[np.argmax(prediction)]
        return predicted_class
    except Exception as e:
        return f"Error: {e}"


In [13]:
def open_file():
    file_path = filedialog.askopenfilename(filetypes=[("Audio Files", "*.wav")])
    if file_path:
        result = predict_audio(file_path)
        messagebox.showinfo("Prediction", f"Predicted Class: {result}")

In [14]:
def record_and_predict():
    try:
        messagebox.showinfo("Recording", "Recording will start now. Please wait for a few seconds...")
        recording = sd.rec(int(SAMPLE_RATE * DURATION), samplerate=SAMPLE_RATE, channels=1, dtype='float32')
        sd.wait()
        temp_wav = tempfile.NamedTemporaryFile(delete=False, suffix=".wav")
        write(temp_wav.name, SAMPLE_RATE, recording)
        result = predict_audio(temp_wav.name)
        messagebox.showinfo("Live Prediction", f"Predicted Class: {result}")
        os.unlink(temp_wav.name)
    except Exception as e:
        messagebox.showerror("Error", str(e))

In [15]:
# Create GUI
app = tk.Tk()
app.title("Gunshot Audio Classifier")
app.geometry("300x200")

''

In [16]:
label = tk.Label(app, text="Choose an audio file or record live:")
label.pack(pady=10)

file_button = tk.Button(app, text="Browse Audio File", command=open_file)
file_button.pack(pady=10)

record_button = tk.Button(app, text="Record Live Audio", command=record_and_predict)
record_button.pack(pady=10)

In [17]:
app.mainloop()

1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 1s/step


In [21]:
# Save model
import joblib
os.makedirs("models", exist_ok=True)
joblib.dump(model, "models/gunshot_model.pkl")
print("✅ Gunshot model trained and saved.")

✅ Gunshot model trained and saved.
